# Imports

In [34]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.linear_model import LinearRegression, Lasso
from sklearn.multioutput import MultiOutputRegressor
from sklearn.model_selection import train_test_split, KFold
from sklearn import metrics
import statsmodels.api as sm

from sklearn.neighbors import KNeighborsRegressor
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.preprocessing import StandardScaler, PolynomialFeatures

from sklearn.tree import DecisionTreeRegressor, plot_tree
from sklearn.ensemble import BaggingRegressor
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV

from sklearn.ensemble import VotingRegressor

from sklearn.ensemble import RandomForestRegressor, ExtraTreesRegressor
from sklearn.ensemble import AdaBoostRegressor, GradientBoostingRegressor


# State Level Models

In [2]:
state_data = pd.read_csv('../Data/merged_state_final.csv')
state_data.head()

Location  Employment_2020  Employment_2021  Employment_2022  \
0     Alabama          2671005          2769464          2869931   
1      Alaska           430840           443047           457687   
2     Arizona          3920033          4086802          4287595   
3    Arkansas          1639829          1686444          1755536   
4  California         23154091         23934549         25300974   

   Inc_Per_Cap_2020  Inc_Per_Cap_2021  Inc_Per_CAp_2022  Life_Exp_2020  \
0             45887             50059             50916           73.2   
1             61898             65662             68635           76.6   
2             52133             56420             58442           76.3   
3             47147             51636             52618           73.8   
4             70061             76991             77036           79.0   

   Life_Exp_2019  Life_Exp_2018  ...  Yes, 50 or more people  all_causes_2020  \
0           75.2           75.1  ...                    1.00             9021   
1           77.7           78.0  ...                    0.00              545   
2           78.8           78.7  ...                    2.89            13186   
3           75.7           75.6  ...                    1.00             4992   
4           80.9           80.8  ...                    1.18            41279   

   all_causes_2021  all_causes_2022  covid_2020  covid_2021  covid_2022  \
0            13018             6246        6337        9771        3933   
1             1429              686         213         804         275   
2            17961             8835        8603       13536        5849   
3             6908             3854        3691        5333        2593   
4            60680            36786       29962       48834       21158   

   Covid_pop_perce_2020  Covid_pop_perce_2021  Covid_pop_perce_2022  
0              0.001261              0.001945              0.000783  
1              0.000290              0.001096              0.000375  
2              0.001203              0.001893              0.000818  
3              0.001226              0.001771              0.000861  
4              0.000758              0.001235              0.000535  

[5 rows x 123 columns]

## Y = Excess Deaths

In [3]:
X1 = state_data.drop(columns=['Location', 'Mask_Mandate','Exc_deaths_2017', 'Exc_deaths_2018','Exc_deaths_2019',
                              'Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022',
                      'all_causes_2020', 'all_causes_2021', 'all_causes_2022', 'covid_2020',
                      'covid_2021', 'covid_2022', 'Covid_pop_perce_2020', 'Covid_pop_perce_2021',
                     'Covid_pop_perce_2022'])
y1 = state_data[['Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022']]

In [4]:
X1_train, X1_test, y1_train, y1_test = train_test_split(X1, y1, random_state=42)

#### Model 1 - Random Forest with Standard Scaler

In [5]:
state_sc = StandardScaler()
X1_train_sc = state_sc.fit_transform(X1_train)
X1_test_sc = state_sc.transform(X1_test)

In [6]:
state_rf1 = RandomForestRegressor()
state_rf1.fit(X1_train, y1_train)
state_rf1.score(X1_train, y1_train), state_rf1.score(X1_test, y1_test)

(0.947623520490089, 0.7475461759360269)

#### Model 2 - Random Forest with Poly and Standard Scaler

In [7]:
state_poly1 = PolynomialFeatures()
X1_train_poly = state_poly1.fit_transform(X1_train)
X1_test_poly = state_poly1.transform(X1_test)

state_sc1 = StandardScaler()
X1_train_polysc = state_sc1.fit_transform(X1_train_poly)
X1_test_polysc = state_sc1.transform(X1_test_poly)

In [8]:
state_rf2 = RandomForestRegressor()
state_rf2.fit(X1_train_polysc, y1_train)
state_rf2.score(X1_train_polysc, y1_train), state_rf2.score(X1_test_polysc, y1_test)

(0.953669771884866, 0.7102485685978867)

#### Model 3 - GradBoosting, MultiOutput & GridSearch with Poly & Standard Scaler

In [9]:
grad = GradientBoostingRegressor()
multi1 = MultiOutputRegressor(grad)

pgrid = {
    'estimator__learning_rate': [0.1, 1, 10],
    'estimator__n_estimators': [10, 100],
    'estimator__max_depth': [None, 1, 2, 3]
}

kf1 = KFold(n_splits=10, shuffle=True, random_state=42)
gs1 = GridSearchCV(multi1, pgrid, cv=kf1, n_jobs=-1)

In [10]:
%%time
gs1.fit(X1_train_polysc, y1_train)

/Users/anaconda3/lib/python3.11/site-packages/sklearn/model_selection/_search.py:987: RuntimeWarning: overflow encountered in square
  (array - array_means[:, np.newaxis]) ** 2, axis=1, weights=weights


CPU times: user 3.98 s, sys: 113 ms, total: 4.09 s
Wall time: 2min 35s


GridSearchCV(cv=KFold(n_splits=10, random_state=42, shuffle=True),
             estimator=MultiOutputRegressor(estimator=GradientBoostingRegressor()),
             n_jobs=-1,
             param_grid={'estimator__learning_rate': [0.1, 1, 10],
                         'estimator__max_depth': [None, 1, 2, 3],
                         'estimator__n_estimators': [10, 100]})

In [12]:
gs1.score(X1_train_polysc, y1_train), gs1.score(X1_test_polysc, y1_test)

(0.9997142568568328, 0.7478307631504935)

## Y = Covid Deaths

In [13]:
X2 = state_data.drop(columns=['Location', 'Mask_Mandate','Exc_deaths_2017', 'Exc_deaths_2018','Exc_deaths_2019',
                              'Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022',
                      'all_causes_2020', 'all_causes_2021', 'all_causes_2022', 'covid_2020',
                      'covid_2021', 'covid_2022', 'Covid_pop_perce_2020', 'Covid_pop_perce_2021',
                     'Covid_pop_perce_2022'])
y2 = state_data[['covid_2020', 'covid_2021', 'covid_2022']]

In [14]:
X2_train, X2_test, y2_train, y2_test = train_test_split(X2, y2, random_state=42)

In [15]:
state_poly2 = PolynomialFeatures()
X2_trainpoly = state_poly2.fit_transform(X2_train)
X2_testpoly = state_poly2.transform(X2_test)

state_ss2 = StandardScaler()
X2_train_polysc = state_ss2.fit_transform(X2_trainpoly)
X2_test_polysc = state_ss2.transform(X2_testpoly)

#### Model 1 - Random Forest with Poly & Standard Scaler

In [16]:
state_rf3 = RandomForestRegressor()
state_rf3.fit(X2_train_polysc, y2_train)
state_rf3.score(X2_train_polysc, y2_train), state_rf3.score(X2_test_polysc, y2_test)

(0.9551495974253245, 0.8092616449500892)

#### Model 2 - KNN with Poly & Standard Scaler

In [17]:
state_knn = KNeighborsRegressor()
state_knn.fit(X2_train_polysc, y2_train)
state_knn.score(X2_train_polysc, y2_train), state_knn.score(X2_test_polysc, y2_test)

(0.7436503805578066, 0.5625614945672842)

#### Model 3 - GradBoost, MultiOutput & GridSearch with Poly & Standard Scaler

In [29]:
grad = GradientBoostingRegressor()
multi2 = MultiOutputRegressor(grad)

pgrid = {
    'estimator__learning_rate': [0.1, 1, 10],
    'estimator__n_estimators': [10, 100, 200, 300],
    'estimator__max_depth': [None, 1, 2, 3]
}

kf1 = KFold(n_splits=10, shuffle=True, random_state=42)
gs2 = GridSearchCV(multi2, pgrid, cv=kf1, n_jobs=-1)

In [30]:
%%time
gs2.fit(X2_train_polysc, y2_train)

/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/numpy/core/fromnumeric.py:86: RuntimeWarning: overflow encountered in reduce
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/numpy/core/fromnumeric.py:86: RuntimeWarning: overflow encountered in reduce
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)
/Users/anaconda3/lib/python3.11/site-packages/sklearn/

/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.1

/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.1

/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.1

  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y

...

/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.1

/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.1

/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.1

CPU times: user 8.9 s, sys: 551 ms, total: 9.46 s
Wall time: 14min 56s


GridSearchCV(cv=KFold(n_splits=10, random_state=42, shuffle=True),
             estimator=MultiOutputRegressor(estimator=GradientBoostingRegressor()),
             n_jobs=-1,
             param_grid={'estimator__learning_rate': [0.1, 1, 10],
                         'estimator__max_depth': [None, 1, 2, 3],
                         'estimator__n_estimators': [10, 100, 200, 300]})

In [31]:
gs2.score(X2_train_polysc, y2_train), gs2.score(X2_test_polysc, y2_test)

(0.9999918872830208, 0.8962131646760821)

In [32]:
gs2.best_params_

{'estimator__learning_rate': 0.1,
 'estimator__max_depth': 1,
 'estimator__n_estimators': 200}

#### Model 4 -  Random Forest, KFold & GridSearch with Poly & Standard Scaler

In [22]:
params = {
    'max_features': np.arange(1, X2.shape[1] + 1), 
    'max_depth': np.append(np.arange(1, 10), None), 
    'min_samples_leaf': np.arange(1, 31) 
}
kf = KFold(n_splits=10, shuffle=True, random_state=2023)
ranfor = RandomForestRegressor(
    n_estimators=100,
    random_state=2023
)

gs2 = GridSearchCV(ranfor, params, cv=kf, n_jobs=-1)

In [25]:
%%time
gs2.fit(X2_train_polysc, y2_train)

CPU times: user 1min 56s, sys: 15.1 s, total: 2min 11s
Wall time: 31min 14s


GridSearchCV(cv=KFold(n_splits=10, random_state=2023, shuffle=True),
             estimator=RandomForestRegressor(random_state=2023), n_jobs=-1,
             param_grid={'max_depth': array([1, 2, 3, 4, 5, 6, 7, 8, 9, None], dtype=object),
                         'max_features': array([  1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,  13,
        14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,  26,
        27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,  39,
        40,  41,  42,  43,  44,  45,  46,  47,  48,  49,  50,  51,  52,
        53,  54,  55,  56,  57,  58,  59,  60,  61,  62,  63,  64,  65,
        66,  67,  68,  69,  70,  71,  72,  73,  74,  75,  76,  77,  78,
        79,  80,  81,  82,  83,  84,  85,  86,  87,  88,  89,  90,  91,
        92,  93,  94,  95,  96,  97,  98,  99, 100, 101, 102, 103, 104,
       105, 106]),
                         'min_samples_leaf': array([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17,
       18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30])})

In [26]:
gs2.score(X2_train_polysc, y2_train), gs2.score(X2_test_polysc, y2_test)

(0.7930247825616247, 0.6592708754598661)

#### Model 5 - LASSO  Model

In [35]:
las = Lasso(max_iter=1000, alpha=0.1)
las.fit(X2_train, y2_train)
las.score(X2_train, y2_train), las.score(X2_test, y2_test)

(0.9999991400245168, 0.9226665134912698)

# County Level Data

In [ ]:
county_data = pd.read_csv('../Data/Cleaned/county_df3.csv')
county_data.head()

## Y = Number of Cases

#### Model 1 - 8 X Variables

In [ ]:
y3 = county_data['cases']
X3 = county_data[['% Physically Inactive', 'Percent Unemployed', 'Average Daily PM2.5', 'Percent Insufficient Sleep', 'Percent Uninsured Adults',
       'Population', 'percent Asian', 'percent Not Proficient in English', 'Masks', 'Administered_Dose1_Pop_Pct']]

# TTS
X3_train, X3_test, y3_train, y3_test = train_test_split(X3, y3, random_state = 42)

In [ ]:
lr_county_cases_lim = LinearRegression()
lr_county_cases_lim.fit(X_train, y_train)

print(f'Train Score: {lr_county_cases_lim.score(X_train, y_train)}')
print(f'Test Score: {lr_county_cases_lim.score(X_test, y_test)}')

In [ ]:
pd.DataFrame(set(zip(X.columns, lr_county_cases_lim.coef_)), columns = ['Variable Name',
                                'Coefficient']).sort_values('Coefficient').round(1).head(5)

#### Random Forest (RF) w/ GradBoost & Random Search CV

In [ ]:
y4 = county_data['cases']
X4 = county_data.drop(columns = ['cases', 'deaths'])

# TTS
X4_train, X4_test, y4_train, y4_test = train_test_split(X4, y4, random_state = 42)

In [ ]:
params = {
    'max_features': np.arange(5, X.shape[1] + 1),
    'max_depth': np.append(np.arange(1, 50), None),
    'min_samples_leaf': [2, 3],   
    'n_estimators': [50, 100, 200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000]
}

rf_gb = GradientBoostingRegressor(random_state = 42)

rf_gb_county_cases = RandomizedSearchCV(rf_gb, params, n_iter=100, cv = 5, n_jobs = -1)

In [ ]:
%%time
rf_gb_county_cases.fit(X_train, y_train)

In [ ]:
print(f'Train Score: {rf_gb_county_cases.score(X4_train, y4_train)}')
print(f'Test Score: {rf_gb_county_cases.score(X4_test, y4_test)}')

In [ ]:
rf_gb_county_cases.best_params_

In [ ]:
pd.DataFrame({'Features': X.columns, 'Importance': rf_gb_county_cases.best_estimator_. \
              feature_importances_}).sort_values('Importance', ascending = False).head(10)

#### Extra Trees (ET) w/ Random Search CV

In [ ]:
params = {
    'max_features': np.arange(5, X.shape[1] + 1),
    'min_samples_leaf': [2, 3],
    'max_depth': [None, 10, 20, 30, 40, 50],
    'n_estimators': [50, 100, 200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000]
}

et = ExtraTreesRegressor(n_estimators = 500, random_state = 42)

et_rs_county_cases = RandomizedSearchCV(et, params, n_iter=100, cv = 5, n_jobs = -1)

In [ ]:
%%time
et_rs_county_cases.fit(X4_train, y4_train)

In [ ]:
print(f'Train Score: {et_rs_county_cases.score(X4_train, y4_train)}')
print(f'Test Score: {et_rs_county_cases.score(X4_test, y4_test)}')

In [ ]:
et_rs_county_cases.best_params_

In [ ]:
pd.DataFrame({'Features': X.columns, 'Importance': et_rs_county_cases.best_estimator_. \
              feature_importances_}).sort_values('Importance', ascending = False).head(10)

## Y = Deaths

#### Model 1 - 8 X-Variables

In [ ]:
y5 = county_data['deaths']
X5 = county_data[['% Physically Inactive', 'Percent Unemployed', 'Average Daily PM2.5',
                  'Percent Insufficient Sleep', 'Percent Uninsured Adults','Population',
                  'percent Asian', 'percent Not Proficient in English', 'Masks',
                  'Administered_Dose1_Pop_Pct']]

# TTS
X5_train, X5_test, y5_train, y5_test = train_test_split(X5, y5, random_state = 42)

In [ ]:
lr_county_deaths_lim = LinearRegression()
lr_county_deaths_lim.fit(X_train, y_train)

print(f'Train Score: {lr_county_deaths_lim.score(X_train, y_train)}')
print(f'Test Score: {lr_county_deaths_lim.score(X_test, y_test)}')

In [ ]:
pd.DataFrame(set(zip(X.columns, lr_county_deaths_lim.coef_)), columns = ['Variable Name', \
                                'Coefficient']).sort_values('Coefficient').round(1).head(5)

#### Model 2 - Random Forest (RF) w/ GradBoost & Random Search CV

In [ ]:
y6 = county_data['deaths']
X6 = county_data.drop(columns = ['cases', 'deaths'])

# TTS
X6_train, X6_test, y6_train, y6_test = train_test_split(X6, y6, random_state = 42)

In [ ]:
params = {
    'max_features': np.arange(5, X.shape[1] + 1),
    'max_depth': np.append(np.arange(1, 50), None),
    'n_estimators': [50, 100, 150, 200, 250, 300, 350, 400, 450, 500]
}

rf_gb = GradientBoostingRegressor(random_state = 42)

rf_gb_county_deaths = RandomizedSearchCV(rf_gb, params, n_iter=100, cv = 5, n_jobs = -1)

In [ ]:
%%time
rf_gb_county_deaths.fit(X6_train, y6_train)

In [ ]:
print(f'Train Score: {rf_gb_county_deaths.score(X_train, y_train)}')
print(f'Test Score: {rf_gb_county_deaths.score(X_test, y_test)}')

In [ ]:
rf_gb_county_deaths.best_params_

In [ ]:
pd.DataFrame({'Features': X6.columns, 'Importance': rf_gb_county_deaths.best_estimator_.\
              feature_importances_}).sort_values('Importance', ascending = False).head(10)